In [1]:
import csv
import os
import sys
import random
import string
import pandas as pd
import pyspark
from nltk.corpus import stopwords  
from nltk.tokenize import word_tokenize, sent_tokenize
from nltk.tokenize import RegexpTokenizer
from pyspark.ml.feature import HashingTF, IDF, Tokenizer, StopWordsRemover
from pyspark.sql import SQLContext
from pyspark.rdd import RDD
from pyspark.sql import Row
from pyspark.sql import DataFrame
from pyspark.sql import SparkSession
from pyspark.sql.functions import desc, size, max, abs

In [2]:
# Initialize a spark session
spark = SparkSession \
    .builder \
    .appName("Python Spark SQL basic example") \
    .config("spark.some.config.option", "some-value") \
    .getOrCreate()

In [16]:
# Label the data sets, remove unncessary fields, sample and save the samples
fake = pd.read_csv("../data/Fake.csv")
fake = fake.assign(label="Fake")
fake = fake.drop(columns=["date", "subject"])
fake = fake.sample(2150)
true = pd.read_csv("../data/True.csv")
true = true.assign(label="True")
true = true.drop(columns=["date", "subject"])
true = true.sample(2150)
# fake.to_csv("../data/Sample_Fake.csv", index=False, header=None)
# true.to_csv("../data/Sample_True.csv", index=False, header=None)

# Extrac the stop words and punctuations and save them to a file
punc = list(string.punctuation) + ['“','”','‘', '’','...','']
stop_punc = stopwords.words('english') + punc
# with open('stop_punc.txt', 'w') as file:
#     file.write(str(stop_punc))

In [20]:
# Tokenizing articles and removing stop words from the article
fake_rdd = spark.read.csv("../data/Sample_Fake.csv").rdd
fake_rdd = fake_rdd.map(lambda x: (x[0] + ' ' + x[1], x[2])).filter(lambda x: x[0] is not None)
fake_rdd = fake_rdd.map(lambda x: Row(article=x[0], label=x[1]))
fake_df = spark.createDataFrame(fake_rdd)
tokenizer = Tokenizer(inputCol="article", outputCol="words")
fake_df = tokenizer.transform(fake_df)
fake_rdd = fake_df.rdd
fake_rdd = fake_rdd.map(lambda x: (x[0], [i for i in x[2] if i not in stop_punc], x[1]))
true_rdd = spark.read.csv("../data/Sample_True.csv").rdd
true_rdd = true_rdd.map(lambda x: (x[0] + ' ' + x[1], x[2])).filter(lambda x:x[0] is not None)
true_rdd = true_rdd.map(lambda x:Row(article=x[0], label=x[1]))
true_df = spark.createDataFrame(true_rdd)
true_df = tokenizer.transform(true_df)
true_rdd = true_df.rdd
true_rdd = true_rdd.map(lambda x: (x[0], [i for i in x[2] if i not in stop_punc], x[1]))

[("Norway's Liberal Party seeks to join government OSLO (Reuters) - Norway s Liberal Party will launch formal negotiations to join the right-wing cabinet of Prime Minister Erna Solberg, it said on Saturday, although the government would still be ruling in a minority even if the small centrist group is included. Informal talks have taken place since the government won re-election in September, and bringing in the Liberals could give a boost to policies favoring small businesses, the environment and education.  We are going to give ourselves a chance ... to find a common platform we can agree on,  Liberal Party leader Trine Skei Grande told a meeting of her party in parliament on Saturday, adding it would be a  challenging and difficult  process. Adding the Liberals to the coalition of the Conservatives and the anti-immigration Progress Party could make day-to-day governing easier for Solberg, although she would still require backing from another small party, the Christian Democrats. The